In [1]:
import pandas as pd
import numpy as np
import statsmodels.api as sm
from scipy import stats
from scipy.stats import zscore
import openpyxl

In [2]:
# Load equity risk premium data, 1973:01-2014:12
input_file = 'Returns_short_interest_data.xlsx'
input_sheet = 'GW variables'

# Read in the data
df = pd.read_excel(input_file, sheet_name=input_sheet, usecols="K,Q", skiprows=1223, nrows=504)
df1 = pd.read_excel(input_file, sheet_name=input_sheet, usecols="K,Q", skiprows=1224, nrows=504)
# Extract the relevant columns
Rfree_lag = df.iloc[:, 0] ## .values 
R_SP500 = df1.iloc[:, 1] ## .values

# Calculate equity risk premium
ER = R_SP500 - Rfree_lag

/Users/jorgenlunner/opt/anaconda3/lib/python3.9/site-packages/openpyxl/worksheet/header_footer.py:48: UserWarning: Cannot parse header or footer so it will be ignored
  warn("""Cannot parse header or footer so it will be ignored""")
/Users/jorgenlunner/opt/anaconda3/lib/python3.9/site-packages/openpyxl/worksheet/_reader.py:312: UserWarning: Unknown extension is not supported and will be removed
  warn(msg)
/Users/jorgenlunner/opt/anaconda3/lib/python3.9/site-packages/openpyxl/worksheet/header_footer.py:48: UserWarning: Cannot parse header or footer so it will be ignored
  warn("""Cannot parse header or footer so it will be ignored""")
/Users/jorgenlunner/opt/anaconda3/lib/python3.9/site-packages/openpyxl/worksheet/_reader.py:312: UserWarning: Unknown extension is not supported and will be removed
  warn(msg)


In [3]:
# Load data
GW = np.load('Program_generate_GW1_predictors.npy')

In [4]:
# Load short interest data, 1973:01-2014:12
EWSI = pd.read_excel(input_file, sheet_name='Short interest', usecols="B", skiprows=0, nrows=504).values.flatten()

# Calculate logarithm of short interest
log_EWSI = np.log(EWSI)

/Users/jorgenlunner/opt/anaconda3/lib/python3.9/site-packages/openpyxl/worksheet/_reader.py:312: UserWarning: Unknown extension is not supported and will be removed
  warn(msg)


In [5]:
# Define horizon 

h = np.array([1, 3, 6, 12])

# Initialize arrays

ER_h = np.empty((len(ER), len(h)))
R_f_h = np.empty((len(ER), len(h)))

# Compute cumulative excess returns

for j in range(len(h)):
    for t in range(len(ER) - (h[j] - 1)):
        ER_h[t, j] = np.prod(1 + R_SP500[t:t + h[j]]) - \
            np.prod(1 + Rfree_lag[t:t + h[j]])
        R_f_h[t, j] = np.prod(1 + Rfree_lag[t:t + h[j]]) - 1

In [6]:
T = len(ER)
in_sample_end = 1989
R = (in_sample_end - 1972) * 12 # in-sample period
P = T - R # out-of-sample period
FC_PM = np.empty((P, len(h)))
w_PM = np.empty((P, len(h)))
R_PM = np.empty((P, len(h)))
ER_PM = np.empty((P, len(h)))
FC_PR = np.empty((P, GW.shape[1]+1, len(h)))
w_PR = np.empty((P, GW.shape[1]+1, len(h)))
R_PR = np.empty((P, GW.shape[1]+1, len(h)))
ER_PR = np.empty((P, GW.shape[1]+1, len(h)))
R_BH = np.empty((P, len(h)))
ER_BH = np.empty((P, len(h)))
FC_vol = np.empty((P, len(h)))
window = 12*10
RRA = 3
w_LB = -0.5
w_UB = 1.5

In [7]:
for p in range(P):
    for j in range(len(h)):
        if R+p-h[j] <= window-1:
            # Compute the sample standard deviation of the first R+p-h[j] elements of column j of ER_h
            FC_vol[p, j] = np.std(ER_h[:R+p-h[j]+1, j], ddof=1)
        else:
            # Compute the sample standard deviation of the last window elements of column j of ER_h
            FC_vol[p, j] = np.std(ER_h[R+p-h[j]-window+1:R+p-h[j]+1, j], ddof=1)
        
        FC_PM[p, j] = np.mean(ER_h[:R + 1+ p - h[j], j])
        for i in range(GW.shape[1] + 1):
            if i <= GW.shape[1] - 1:
                X_i_j_p = np.concatenate((np.ones((R + p - h[j], 1)), GW[0:R + p - h[j], i:i+1]), axis=1)
                results_i_j_p = np.linalg.lstsq(X_i_j_p, ER_h[1:R+p-h[j]+1, j], rcond=None)
                FC_PR[p, i, j] = np.array([1, GW[R+p-1, i]]).dot(results_i_j_p[0])
            else:
                trend_p = np.arange(1, R+p+1)
                X_linear_p = np.concatenate((np.ones((R+p, 1)), trend_p.reshape(-1,1)), axis=1)
                model_linear_p = sm.OLS(log_EWSI[:R+p], X_linear_p)
                results_linear_p = model_linear_p.fit()
                SII_p = zscore(results_linear_p.resid, ddof=1)
                X_SII_j_p = np.concatenate([np.ones((R+p-h[j], 1)), SII_p[0:R+p-h[j]].reshape(-1, 1)], axis=1)
                model_SII_j_p = sm.OLS(ER_h[1:R+p+1-h[j], j].reshape(-1,1), X_SII_j_p)
                results_SII_j_p = model_SII_j_p.fit()
                FC_PR[p, i, j] = np.array([1, SII_p[-1]]).dot(results_SII_j_p.params)                

In [8]:
# Computing portfolio weights/returns

for j in range(len(h)):
    for t in range(1, int(P/h[j])+1):
        FC_vol_j_t = FC_vol[(t-1)*h[j], j]
        FC_PM_j_t = FC_PM[(t-1)*h[j], j]
        w_PM_j_t = (1/RRA) * FC_PM_j_t / FC_vol_j_t**2

        if w_PM_j_t > w_UB:
            w_PM[(t-1)*h[j], j] = w_UB
        elif w_PM_j_t < w_LB:
            w_PM[(t-1)*h[j], j] = w_LB
        else:
            w_PM[(t-1)*h[j], j] = w_PM_j_t

        R_PM[(t-1)*h[j], j] = R_f_h[R+(t-1)*h[j], j] + w_PM[(t-1)*h[j], j] * ER_h[R+(t-1)*h[j], j]
        ER_PM[(t-1)*h[j], j] = R_PM[(t-1)*h[j], j] - R_f_h[R+(t-1)*h[j], j]

        for i in range(FC_PR.shape[1]):
            FC_PR_i_j_t = FC_PR[(t-1)*h[j], i, j]
            w_PR_i_j_t = (1/RRA) * FC_PR_i_j_t / FC_vol_j_t**2

            if w_PR_i_j_t > w_UB:
                w_PR[(t-1)*h[j], i, j] = w_UB
            elif w_PR_i_j_t < w_LB:
                w_PR[(t-1)*h[j], i, j] = w_LB
            else:
                w_PR[(t-1)*h[j], i, j] = w_PR_i_j_t

            R_PR[(t-1)*h[j], i, j] = R_f_h[R+(t-1)*h[j], j] + w_PR[(t-1)*h[j], i, j] * ER_h[R+(t-1)*h[j], j]
            ER_PR[(t-1)*h[j], i, j] = R_PR[(t-1)*h[j], i, j] - R_f_h[R+(t-1)*h[j], j]

        R_BH[(t-1)*h[j], j] = R_f_h[R+(t-1)*h[j], j] + ER_h[R+(t-1)*h[j], j]
        ER_BH[(t-1)*h[j], j] = ER_h[R+(t-1)*h[j], j]



In [9]:
# Compute CER gains and Sharpe ratios for full OOS period

CER_gain = np.full((FC_PR.shape[1] + 1, len(h)), np.nan)
Sharpe = np.full((FC_PR.shape[1] + 2, len(h)), np.nan)

for j in range(len(h)):
    R_PM_j = R_PM[:, j]
    threshold1 = 0.000001
    threshold2= 1.01
    R_PM_j = R_PM_j[(np.isfinite(R_PM_j)) & (np.abs(R_PM_j) > threshold1) & (np.abs(R_PM_j) <= threshold2)]
    ER_PM_j = ER_PM[:, j]
    ER_PM_j = ER_PM_j[np.isfinite(ER_PM_j) & (np.abs(ER_PM_j) > threshold1) & (np.abs(ER_PM_j) <= threshold2)]
    CER_PM_j = (12 / h[j]) * (np.mean(R_PM_j) - 0.5 * RRA * np.std(R_PM_j, ddof=1) ** 2)
    Sharpe[0, j] = np.sqrt((12 / h[j])) * np.mean(ER_PM_j) / np.std(ER_PM_j, ddof=1)
    
    for i in range(FC_PR.shape[1]):
        R_PR_i_j = R_PR[:, i, j]
        R_PR_i_j = R_PR_i_j[np.isfinite(R_PR_i_j) & (np.abs(R_PR_i_j) > threshold1) & (np.abs(R_PR_i_j) <= threshold2)]
        ER_PR_i_j = ER_PR[:, i, j]
        ER_PR_i_j = ER_PR_i_j[np.isfinite(ER_PR_i_j)& (np.abs(ER_PR_i_j) > threshold1) & (np.abs(ER_PR_i_j) <= threshold2)]
        CER_PR_i_j = (12 / h[j]) * (np.mean(R_PR_i_j) - 0.5 * RRA * np.std(R_PR_i_j, ddof=1) ** 2)
        CER_gain[i, j] = 100 * (CER_PR_i_j - CER_PM_j)
        Sharpe[i + 1, j] = np.sqrt((12 / h[j])) * np.mean(ER_PR_i_j) / np.std(ER_PR_i_j, ddof=1)
    
    R_BH_j = R_BH[:, j]
    R_BH_j = R_BH_j[np.isfinite(R_BH_j) & (np.abs(R_BH_j) > threshold1) & (np.abs(R_BH_j) <= threshold2)]
    ER_BH_j = ER_BH[:, j]
    ER_BH_j = ER_BH_j[np.isfinite(ER_BH_j)& (np.abs(ER_BH_j) > threshold1) & (np.abs(ER_BH_j) <= threshold2)]
    CER_BH_j = (12 / h[j]) * (np.mean(R_BH_j) - 0.5 * RRA * np.std(R_BH_j, ddof=1) ** 2)
    CER_gain[-1, j] = 100 * (CER_BH_j - CER_PM_j)
    Sharpe[-1, j] = np.sqrt((12 / h[j])) * np.mean(ER_BH_j) / np.std(ER_BH_j,ddof=1)

In [10]:
# Compute CER gains and Sharpe ratios for Global Financial Crisis period

GFC_start = (2006 - 1989) * 12 + 1

CER_gain_GFC = np.full((FC_PR.shape[1] + 1, len(h)), np.nan)
Sharpe_GFC = np.full((FC_PR.shape[1] + 2, len(h)), np.nan)


for j in range(len(h)):
    R_PM_j = R_PM[GFC_start - 1:, j]
    R_PM_j = R_PM_j[np.isfinite(R_PM_j) & (np.abs(R_PM_j) > threshold1) & (np.abs(R_PM_j) <= threshold2)]
    ER_PM_j = ER_PM[GFC_start - 1:, j]
    ER_PM_j = ER_PM_j[np.isfinite(ER_PM_j)& (np.abs(ER_PM_j) > threshold1) & (np.abs(ER_PM_j) <= threshold2)]
    CER_PM_j = (12 / h[j]) * (np.mean(R_PM_j) - 0.5 * RRA * np.std(R_PM_j, ddof=1)**2)
    Sharpe_GFC[0, j] = np.sqrt((12 / h[j])) * np.mean(ER_PM_j) / np.std(ER_PM_j, ddof=1)

    for i in range(FC_PR.shape[1]):
        R_PR_i_j = R_PR[GFC_start - 1:, i, j]
        R_PR_i_j = R_PR_i_j[np.isfinite(R_PR_i_j)& (np.abs(R_PR_i_j) > threshold1) & (np.abs(R_PR_i_j) <= threshold2)]
        ER_PR_i_j = ER_PR[GFC_start - 1:, i, j]
        ER_PR_i_j = ER_PR_i_j[np.isfinite(ER_PR_i_j)& (np.abs(ER_PR_i_j) > threshold1) & (np.abs(ER_PR_i_j) <= threshold2)]
        CER_PR_i_j = (12 / h[j]) * (np.mean(R_PR_i_j) - 0.5 * RRA * np.std(R_PR_i_j, ddof=1)**2)
        CER_gain_GFC[i, j] = 100 * (CER_PR_i_j - CER_PM_j)
        Sharpe_GFC[i + 1, j] = np.sqrt((12 / h[j])) * np.mean(ER_PR_i_j) / np.std(ER_PR_i_j, ddof=1)

    R_BH_j = R_BH[GFC_start - 1:, j]
    R_BH_j = R_BH_j[np.isfinite(R_BH_j) & (np.abs(R_BH_j) > threshold1) & (np.abs(R_BH_j) <= threshold2)]
    ER_BH_j = ER_BH[GFC_start - 1:, j]
    ER_BH_j = ER_BH_j[np.isfinite(ER_BH_j) & (np.abs(ER_BH_j) > threshold1) & (np.abs(ER_BH_j) <= threshold2)]
    CER_BH_j = (12 / h[j]) * (np.mean(R_BH_j) - 0.5 * RRA * np.std(R_BH_j, ddof=1)**2)
    CER_gain_GFC[-1, j] = 100 * (CER_BH_j - CER_PM_j)
    Sharpe_GFC[-1, j] = np.sqrt((12 / h[j])) * np.mean(ER_BH_j) / np.std(ER_BH_j, ddof=1)

In [11]:
# Compute CER gains and Sharpe ratios for pre-crisis period

CER_gain_pre = np.full((FC_PR.shape[1] + 1, len(h)), np.nan)
Sharpe_pre = np.full((FC_PR.shape[1] + 2, len(h)), np.nan)

for j in range(len(h)):
    R_PM_j = R_PM[:GFC_start - 1, j]
    R_PM_j = R_PM_j[np.isfinite(R_PM_j) & (np.abs(R_PM_j) > threshold1) & (np.abs(R_PM_j) <= threshold2)]
    ER_PM_j = ER_PM[:GFC_start - 1, j]
    ER_PM_j = ER_PM_j[np.isfinite(ER_PM_j)& (np.abs(ER_PM_j) > threshold1) & (np.abs(ER_PM_j) <= threshold2)]
    CER_PM_j = (12 / h[j]) * (np.mean(R_PM_j) - 0.5 * RRA * np.std(R_PM_j, ddof=1)**2)
    Sharpe_pre[0, j] = np.sqrt((12 / h[j])) * np.mean(ER_PM_j) / np.std(ER_PM_j, ddof=1)

    for i in range(FC_PR.shape[1]):
        R_PR_i_j = R_PR[:GFC_start - 1, i, j]
        R_PR_i_j = R_PR_i_j[np.isfinite(R_PR_i_j) & (np.abs(R_PR_i_j) > threshold1) & (np.abs(R_PR_i_j) <= threshold2)]
        ER_PR_i_j = ER_PR[:GFC_start - 1, i, j]
        ER_PR_i_j = ER_PR_i_j[np.isfinite(ER_PR_i_j) & (np.abs(ER_PR_i_j) > threshold1) & (np.abs(ER_PR_i_j) <= threshold2)]
        CER_PR_i_j = (12 / h[j]) * (np.mean(R_PR_i_j) - 0.5 * RRA * np.std(R_PR_i_j, ddof=1)**2)
        CER_gain_pre[i, j] = 100 * (CER_PR_i_j - CER_PM_j)
        Sharpe_pre[i + 1, j] = np.sqrt((12 / h[j])) * np.mean(ER_PR_i_j) / np.std(ER_PR_i_j, ddof=1)

    R_BH_j = R_BH[:GFC_start - 1, j]
    R_BH_j = R_BH_j[np.isfinite(R_BH_j) & (np.abs(R_BH_j) > threshold1) & (np.abs(R_BH_j) <= threshold2)]
    ER_BH_j = ER_BH[:GFC_start - 1, j]
    ER_BH_j = ER_BH_j[np.isfinite(ER_BH_j) & (np.abs(ER_BH_j) > threshold1) & (np.abs(ER_BH_j) <= threshold2)]
    CER_BH_j = (12 / h[j]) * (np.mean(R_BH_j) - 0.5 * RRA * np.std(R_BH_j, ddof=1)**2)
    CER_gain_pre[-1, j] = 100 * (CER_BH_j - CER_PM_j)
    Sharpe_pre[-1, j] = np.sqrt((12 / h[j])) * np.mean(ER_BH_j) / np.std(ER_BH_j, ddof=1)

In [12]:
# Compute CER gains and Sharpe ratios for post-crisis period
PGFC_start = (2008 - 1989) * 12 + 1

CER_gain_post = np.full((FC_PR.shape[1] + 1, len(h)), np.nan)
Sharpe_post = np.full((FC_PR.shape[1] + 2, len(h)), np.nan)


for j in range(len(h)):
    R_PM_j = R_PM[PGFC_start - 1:, j]
    R_PM_j = R_PM_j[np.isfinite(R_PM_j) & (np.abs(R_PM_j) > threshold1) & (np.abs(R_PM_j) <= threshold2)]
    ER_PM_j = ER_PM[PGFC_start - 1:, j]
    ER_PM_j = ER_PM_j[np.isfinite(ER_PM_j)& (np.abs(ER_PM_j) > threshold1) & (np.abs(ER_PM_j) <= threshold2)]
    CER_PM_j = (12 / h[j]) * (np.mean(R_PM_j) - 0.5 * RRA * np.std(R_PM_j, ddof=1)**2)
    Sharpe_post[0, j] = np.sqrt((12 / h[j])) * np.mean(ER_PM_j) / np.std(ER_PM_j, ddof=1)

    for i in range(FC_PR.shape[1]):
        R_PR_i_j = R_PR[PGFC_start - 1:, i, j]
        R_PR_i_j = R_PR_i_j[np.isfinite(R_PR_i_j)& (np.abs(R_PR_i_j) > threshold1) & (np.abs(R_PR_i_j) <= threshold2)]
        ER_PR_i_j = ER_PR[PGFC_start - 1:, i, j]
        ER_PR_i_j = ER_PR_i_j[np.isfinite(ER_PR_i_j)& (np.abs(ER_PR_i_j) > threshold1) & (np.abs(ER_PR_i_j) <= threshold2)]
        CER_PR_i_j = (12 / h[j]) * (np.mean(R_PR_i_j) - 0.5 * RRA * np.std(R_PR_i_j, ddof=1)**2)
        CER_gain_post[i, j] = 100 * (CER_PR_i_j - CER_PM_j)
        Sharpe_post[i + 1, j] = np.sqrt((12 / h[j])) * np.mean(ER_PR_i_j) / np.std(ER_PR_i_j, ddof=1)

    R_BH_j = R_BH[PGFC_start - 1:, j]
    R_BH_j = R_BH_j[np.isfinite(R_BH_j) & (np.abs(R_BH_j) > threshold1) & (np.abs(R_BH_j) <= threshold2)]
    ER_BH_j = ER_BH[PGFC_start - 1:, j]
    ER_BH_j = ER_BH_j[np.isfinite(ER_BH_j) & (np.abs(ER_BH_j) > threshold1) & (np.abs(ER_BH_j) <= threshold2)]
    CER_BH_j = (12 / h[j]) * (np.mean(R_BH_j) - 0.5 * RRA * np.std(R_BH_j, ddof=1)**2)
    CER_gain_post[-1, j] = 100 * (CER_BH_j - CER_PM_j)
    Sharpe_post[-1, j] = np.sqrt((12 / h[j])) * np.mean(ER_BH_j) / np.std(ER_BH_j, ddof=1)

In [13]:
# Write results to excel file 
output_file = 'Returns_short_interest_results.xlsx'
output_sheet = 'Asset allocation'

with pd.ExcelWriter(output_file, engine='openpyxl', mode='a', if_sheet_exists='overlay') as writer:
    pd.DataFrame(CER_gain).to_excel(writer, sheet_name=output_sheet, startrow=5, startcol=1, header=False, index=False)
    pd.DataFrame(Sharpe).to_excel(writer, sheet_name=output_sheet, startrow=28, startcol=1, header=False, index=False)
    pd.DataFrame(CER_gain_GFC).to_excel(writer, sheet_name=output_sheet, startrow=5, startcol=6, header=False, index=False)
    pd.DataFrame(Sharpe_GFC).to_excel(writer, sheet_name=output_sheet, startrow=28, startcol=6, header=False, index=False)
    pd.DataFrame(CER_gain_pre).to_excel(writer, sheet_name=output_sheet, startrow=5, startcol=11, header=False, index=False)
    pd.DataFrame(Sharpe_pre).to_excel(writer, sheet_name=output_sheet, startrow=28, startcol=11, header=False, index=False)
    pd.DataFrame(CER_gain_post).to_excel(writer, sheet_name=output_sheet, startrow=5, startcol=16, header=False, index=False)
    pd.DataFrame(Sharpe_post).to_excel(writer, sheet_name=output_sheet, startrow=28, startcol=16, header=False, index=False)

In [14]:
# Write results to excel file 
output_file = 'Returns_short_interest_results.xlsx'
output_sheet = 'Asset allocation figures'
with pd.ExcelWriter(output_file, engine='openpyxl', mode='a', if_sheet_exists='overlay') as writer:
    pd.DataFrame(w_PR[:,18,0]).to_excel(writer, sheet_name=output_sheet, startrow=5, startcol=3, header=False, index=False)
    pd.DataFrame(w_PM[:,0]).to_excel(writer, sheet_name=output_sheet, startrow=5, startcol=4, header=False, index=False)
    pd.DataFrame(R_PM[:,0]).to_excel(writer, sheet_name=output_sheet, startrow=5, startcol=8, header=False, index=False)
    pd.DataFrame(R_PR[:,18,0]).to_excel(writer, sheet_name=output_sheet, startrow=5, startcol=7, header=False, index=False)